# Parallelization
The aim of this notebook is to parallelize the training of the models define in the notebook Raman_model_Pytorch.

## Librairies

In [4]:
# --- Utils librairies ---
#Generics librairies
import os
import os.path
from os import path
import numpy as np
import copy
import pickle
from statistics import mean
import matplotlib.pyplot as plt

#Measure librairies
import time

#Dataset librairies
import pandas as pd

# --- DL librairies ---
#Pytorch librairies
import torch
import torch.nn as nn
from torch.optim import Adam
from torch.optim.lr_scheduler import ReduceLROnPlateau
from torch.utils.data import Dataset, DataLoader
import torch.distributed as dist
import torch.optim as optim
import torch.multiprocessing as mp
from torch.nn.parallel import DistributedDataParallel as DDP

#Sklearn librairies
from sklearn.model_selection import LeaveOneGroupOut, train_test_split
from sklearn.metrics import accuracy_score

## GPUs environment

In [5]:
os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID";
os.environ["CUDA_VISIBLE_DEVICES"]="1,2,3,4";
gpus_list = [0, 1, 2, 3]

print(torch.cuda.is_available())
print(torch.cuda.device_count())

True
4


## Data

### Load data 

In [6]:
df, labels, names = pd.read_pickle("../data/dataset_COVID_RAW.pkl")
df = pd.DataFrame(df)
labels = pd.Series(labels, name = 'label')
names = pd.Series(names, name = 'names')
df = pd.concat((df, labels, names), axis = 1)

In [7]:
X_set = df.drop(columns = ['label', "names"]).values
Y_set = df.label.values
groups = df.names.values

In [8]:
folds = list(LeaveOneGroupOut().split(X_set, Y_set, groups = groups))

### Data augmentation

In [9]:
def dataAugment(signal, betashift = 0.24039033704204857, slopeshift = 0.5640435054299953, multishift = 0.0013960388613510225):
    #baseline shift
    beta = np.random.random(size=(signal.shape[0],1))*2*betashift-betashift
    slope = np.random.random(size=(signal.shape[0],1))*2*slopeshift-slopeshift + 1
    #relative positions
    axis = np.array(range(signal.shape[1]))/float(signal.shape[1])
    #offset
    offset = slope*(axis) + beta - axis - slope/2. + 0.5

    #multiplicative coefficient
    multi = np.random.random(size=(signal.shape[0],1))*2*multishift-multishift + 1
    augmented_signal = multi*signal + offset

    return augmented_signal

### Creation of sets

In [10]:
class RamanDataset(Dataset):
    def __init__(self, X, Y):
        super(RamanDataset).__init__()
        x = torch.from_numpy(X)
        self.raman_spectra = x
        y = torch.from_numpy(Y)
        self.labels = y
        
    def __len__(self):
        return len(self.raman_spectra)
    
    def __getitem__(self, idx):
        spectrum = self.raman_spectra[idx]
        label = self.labels[idx]
        
        return spectrum, label

In [11]:
class Datasets(Dataset):
    def __init__(self, ramanDatasets):
        super(Datasets).__init__()
        self.datasets = ramanDatasets
        
    def __len__(self):
        return len(self.datasets)
    
    def __getitem__(self, idx):
        return self.datasets[idx]

In [12]:
def setsCreation(pathToFile, X_set, Y_set, folds):
    if not path.exists(pathToFile):
        train_set = []
        validation_set = []
        test_set = []
        X_train = []
        X_val = []
        X_test = []
        Y_train = []
        Y_val = []
        Y_test = []
        
        for i, (train_idx, test_idx) in enumerate(folds):
            X_train_tmp = X_set[train_idx]
            Y_train_tmp = Y_set[train_idx]
            
            X_test_tmp = X_set[test_idx]
            Y_test_tmp = Y_set[test_idx]
            
            X_train_tmp, X_val_tmp, Y_train_tmp, Y_val_tmp = train_test_split(X_train_tmp, Y_train_tmp, test_size = .1,
                                                                              stratify = Y_train_tmp)
            augment = 30
            augmented_data = []
            Y_list = copy.copy(Y_train_tmp)
            for i in range(augment):
                augmented_data.append(dataAugment(X_train_tmp))
            for i in range(augment-1):
                Y_list = np.concatenate((Y_list, Y_train_tmp), axis=0)
                
            X_train_tmp = np.vstack(augmented_data)
            Y_train_tmp = copy.copy(Y_list)
            train_set_tmp = RamanDataset(X_train_tmp, Y_train_tmp)
            train_set.append(train_set_tmp)
            val_set_tmp = RamanDataset(X_val_tmp, Y_val_tmp)
            validation_set.append(val_set_tmp)
            test_set_tmp = RamanDataset(X_test_tmp, Y_test_tmp)
            test_set.append(test_set_tmp)
        
        train_dataset = Datasets(train_set)
        validation_dataset = Datasets(validation_set)
        test_dataset = Datasets(test_set)
        training_settings = (train_dataset, validation_dataset, test_dataset)
        
        with open(pathToFile, "wb") as outf:
            pickle.dump(training_settings, outf)
        
    else:
        with open(pathToFile, "rb") as inf:
            train_dataset, validation_dataset, test_dataset = pickle.load(inf)
            
    return train_dataset, validation_dataset, test_dataset

In [13]:
train_dataset, validation_dataset, test_dataset = setsCreation("../train_settings/training_settings_cov_raw.pckl", X_set, Y_set, folds)

## Model

In [14]:
class ConvNet(nn.Module):
    def __init__(self):
        super(ConvNet, self).__init__()
        
        self.cnn_layers = nn.Sequential(
            nn.Conv1d(1, 100, kernel_size=100,
                     stride=1, padding_mode='replicate'),
            nn.ReLU(),
            nn.BatchNorm1d(100, eps=0.001, momentum=0.99),
            nn.Conv1d(100, 102, kernel_size=5,
                     stride=2, padding_mode='replicate'),
            nn.ReLU(),
            nn.MaxPool1d(6, stride=3),
            nn.BatchNorm1d(102, eps=0.001, momentum=0.99),
            nn.Conv1d(102, 25, kernel_size=9,
                     stride=5, padding_mode='replicate'),
            nn.ReLU(),
            nn.MaxPool1d(3, stride=2)
        )
        
        self.dense_layers = nn.Sequential(
            nn.Dropout(p=0.1),
            nn.Linear(325, 732),
            nn.LeakyReLU(),
            nn.Dropout(p=0.7000000000000001),
            nn.Linear(732, 152),
            nn.LeakyReLU(),
            nn.Dropout(p=0.25),
            nn.Linear(152,189),
            nn.LeakyReLU(),
            nn.Dropout(p=0.1),
            nn.Linear(189, 3),
            nn.Softmax(dim=1)
        )
        
    def forward(self, x):
        x = x.resize_(x.shape[0],  1, x.shape[1])
        x = self.cnn_layers(x)
        x = torch.flatten(x, 1)
        x = self.dense_layers(x)
        return x

## Pseudo-parallelization

### Utility functions

In [12]:
def createCNN(gpu_ids):
    model = ConvNet()
    model = model.double()
    optimizer = Adam(model.parameters(), lr=0.00020441990333108206)
    loss = nn.CrossEntropyLoss()
    
    if torch.cuda.is_available():
        cuda='cuda:'+str(gpu_ids[0])
        model = nn.DataParallel(model, device_ids=gpu_ids)
        loss.cuda()
    device = torch.device(cuda if torch.cuda.is_available() else 'cpu')
    model.to(device)
    return model, loss, optimizer, device

In [13]:
def train(devices, models, losses, optimizers, train_dataset, validation_dataset, epochs, patience, paths, verbose=0, batch_size=338):
    train_losses = [[] for _ in range(len(models))]
    val_losses = [[] for _ in range(len(models))]
    train_acc = [[] for _ in range(len(models))]
    val_acc = [[] for _ in range(len(models))]
    
    min_val_losses = [np.Inf for _ in range(len(models))]
    max_val_accs = [np.NINF for _ in range(len(models))]
    cum_min_val_loss = np.Inf
    cum_max_val_acc = np.NINF
    epochs_no_improve_loss = 0
    epochs_no_improve_acc = 0
    
    schedulers = []
    training_generators = []
    validation_generators = []
    if verbose == 1:
        verbScheduler = True
    else:
        verbScheduler = False
    for m in range(len(models)) :
        schedulers.append(ReduceLROnPlateau(optimizers[m], factor=0.5, patience=80, cooldown=10, verbose=verbScheduler))
        training_generators.append(DataLoader(train_dataset[m], batch_size=batch_size))
        validation_generators.append(DataLoader(validation_dataset[m], batch_size=batch_size))
        models[m].train()
        
    for epoch in range(epochs):
        cum_val_loss = 0
        cum_val_acc = 0
        if verbose == 1:
            print("------------------------- Epoch {} -------------------------".format(epoch+1))
        for m in range(len(models)):
            loss_train_epoch = []
            acc_train_epoch = []
            for i, (ramanSpectraTrain, labelTrain) in enumerate(training_generators[m]):
                ramanSpectraTrain = ramanSpectraTrain.to(devices[m])
                labelTrain = labelTrain.to(devices[m])
                
                optimizers[m].zero_grad()
                
                output_train = models[m](ramanSpectraTrain)
                
                loss_train = losses[m](output_train, labelTrain)
                loss_train_epoch.append(loss_train.cpu().item())
                
                loss_train.backward()
                optimizers[m].step()
                
                output_label = torch.argmax(output_train, dim=1)
                acc_train = accuracy_score(labelTrain.cpu().detach().numpy(), output_label.cpu().detach().numpy())
                acc_train_epoch.append(acc_train)
                
            tl = mean(loss_train_epoch)
            train_losses[m].append(tl)
            ta = mean(acc_train_epoch)
            train_acc[m].append(ta)
            
            with torch.no_grad():
                loss_val_epoch = []
                acc_val_epoch = []
                for j, (ramanSpectraVal, labelVal) in enumerate(validation_generators[m]):
                    ramanSpectraVal = ramanSpectraVal.to(devices[m])
                    labelVal = labelVal.to(devices[m])
                    
                    output_val = models[m](ramanSpectraVal)
                    
                    loss_val = losses[m](output_val, labelVal)
                    loss_val_epoch.append(loss_val.cpu().item())
                    
                    val_label = torch.argmax(output_val, dim=1)
                    acc_val = accuracy_score(labelVal.cpu().detach().numpy(), val_label.cpu().detach().numpy())
                    acc_val_epoch.append(acc_val)
                    
            vl = mean(loss_val_epoch)
            val_losses[m].append(vl)
            va = mean(acc_val_epoch)
            val_acc[m].append(va)
            
            if vl < min_val_losses[m] or va < max_val_accs[m]:
                torch.save({'model_state_dict' : models[m].state_dict(),
                       'optimizer_state_dict' : optimizers[m].state_dict(),
                       'train_loss' : train_losses[m],
                       'train_acc' : train_acc[m],
                       'val_loss' : val_losses[m],
                       'val_acc' : val_acc[m]}, paths[m])
                if vl < min_val_losses[m]:
                    min_val_losses[m] = vl
                else:
                    max_val_accs[m] = va
            
            cum_val_loss += vl
            cum_val_acc += va
            
            schedulers[m].step(vl)
            
            if verbose == 1:
                print("Model {}:\t train loss : {}; train accuracy : {}; \n validation loss : {}; validation accuracy : {}".format(m+1, tl, ta, vl, va))
    
        
        if cum_val_loss < cum_min_val_loss:
            epochs_no_improve_loss = 0
            cum_min_val_loss = cum_val_loss
        else:
            epochs_no_improve_loss += 1
            
        if cum_val_acc > cum_max_val_acc:
            epochs_no_improve_acc = 0
            cum_max_val_acc = cum_val_acc
        else:
            epochs_no_improve_acc += 1
            
        if epochs_no_improve_acc >= patience and epochs_no_improve_loss >= patience:
            print("Early stopping at epoch {}".format(epoch+1))
            break
            
    for m in range(len(models)):
        checkpoint = torch.load(paths[m])
        models[m].load_state_dict(checkpoint['model_state_dict'])
        optimizers[m].load_state_dict(checkpoint['optimizer_state_dict'])
        train_losses[m] = checkpoint['train_loss']
        train_acc[m] = checkpoint['train_acc']
        val_losses[m] = checkpoint['val_loss']
        val_acc[m] = checkpoint['val_acc']
    
        if verbose == 1:
            print("------------------------- Final result of the model {} ! -------------------------".format(m+1))
            print("Train loss : {}; Train accuracy : {}; \n Validation loss : {}; Validation accuracy : {}".format(train_losses[m][-1], train_acc[m][-1], val_losses[m][-1], val_acc[m][-1]))
        
    return train_losses, val_losses, train_acc, val_acc

In [14]:
def testModel(model, test_set, device, batch_size=1):
    test_acc = []
    test_generator = DataLoader(test_set, batch_size=batch_size)
    model.eval()
    for i, (ramanSpectra, label) in enumerate(test_generator):
        ramanSpectra = ramanSpectra.to(device)
        label = label.to(device)
        
        labelPredict = model(ramanSpectra)
        labelPredict = torch.argmax(labelPredict, dim=1)
        
        acc = accuracy_score(label.cpu().detach().numpy(), labelPredict.cpu().detach().numpy())
        test_acc.append(acc)
    
    return test_acc

### Train part

In [15]:
num_epochs = 273
patience = 50
models = []
optimizers = []
losses = []
devices = []
paths = []

start = time.time()
for i in range(len(train_dataset)):
    model, loss, optimizer, device = createCNN(gpus_list)
    models.append(model)
    optimizers.append(optimizer)
    losses.append(loss)
    devices.append(device)
    path = "../saved_models/covid_RAW/"+str(i+1)+".pckl"
    paths.append(path)
    
train_losses, val_losses, train_accs, val_accs = train(devices, models, losses, optimizers, train_dataset, validation_dataset, num_epochs, patience, paths, verbose=1)
end = time.time()

------------------------- Epoch 1 -------------------------
Model 1:	 train loss : 1.095839331193381; train accuracy : 0.4053053173932295; 
 validation loss : 1.0866709496276956; validation accuracy : 0.4791666666666667
Model 2:	 train loss : 1.0974993198681198; train accuracy : 0.3597730940388283; 
 validation loss : 1.0922830096330811; validation accuracy : 0.40585774058577406
Model 3:	 train loss : 1.0976469444339805; train accuracy : 0.33075044613506155; 
 validation loss : 1.0934703991612764; validation accuracy : 0.3682008368200837
Model 4:	 train loss : 1.0932921691430129; train accuracy : 0.38728025559837814; 
 validation loss : 1.0883922002467439; validation accuracy : 0.3807531380753138
Model 5:	 train loss : 1.0933410029856703; train accuracy : 0.3246924016154785; 
 validation loss : 1.0901828846089803; validation accuracy : 0.3179916317991632
Model 6:	 train loss : 1.0957012793130343; train accuracy : 0.34484746023207563; 
 validation loss : 1.0889408312443833; validation a

Model 52:	 train loss : 1.09178334137616; train accuracy : 0.3349139915744043; 
 validation loss : 1.080802502055079; validation accuracy : 0.3263598326359833
Model 53:	 train loss : 1.0945691820539292; train accuracy : 0.32293700993966246; 
 validation loss : 1.0883059062099725; validation accuracy : 0.3305439330543933
Model 54:	 train loss : 1.0948216752905846; train accuracy : 0.3314548699164084; 
 validation loss : 1.0887103267260032; validation accuracy : 0.33472803347280333
Model 55:	 train loss : 1.0958866940308793; train accuracy : 0.36338793832162536; 
 validation loss : 1.0926656951986167; validation accuracy : 0.3682008368200837
Model 56:	 train loss : 1.0979041192397645; train accuracy : 0.3548887010425472; 
 validation loss : 1.0918907865221743; validation accuracy : 0.39330543933054396
Model 57:	 train loss : 1.0933026017634426; train accuracy : 0.3336244175405015; 
 validation loss : 1.0871000356124663; validation accuracy : 0.3054393305439331
Model 58:	 train loss : 1.0

Model 2:	 train loss : 1.0863889065806247; train accuracy : 0.4184486841829499; 
 validation loss : 1.080180844529889; validation accuracy : 0.39748953974895396
Model 3:	 train loss : 1.0872253639071543; train accuracy : 0.3969662815816662; 
 validation loss : 1.0849482346200918; validation accuracy : 0.3472803347280335
Model 4:	 train loss : 1.0794740195471833; train accuracy : 0.4198461251916272; 
 validation loss : 1.0810869195155484; validation accuracy : 0.39748953974895396
Model 5:	 train loss : 1.0808677616492828; train accuracy : 0.32647694186155723; 
 validation loss : 1.0772243004225637; validation accuracy : 0.34309623430962344
Model 6:	 train loss : 1.0827599426973904; train accuracy : 0.4390120369141348; 
 validation loss : 1.0703938248095146; validation accuracy : 0.4560669456066946
Model 7:	 train loss : 1.0774190800232195; train accuracy : 0.3999030987773952; 
 validation loss : 1.0824858076474395; validation accuracy : 0.3514644351464435
Model 8:	 train loss : 1.079050

Model 53:	 train loss : 1.081635446242064; train accuracy : 0.32547293555251117; 
 validation loss : 1.0800490297176726; validation accuracy : 0.3305439330543933
Model 54:	 train loss : 1.0845684204104984; train accuracy : 0.3318775241852165; 
 validation loss : 1.0732139302013264; validation accuracy : 0.3305439330543933
Model 55:	 train loss : 1.0843692844378943; train accuracy : 0.3613475384032413; 
 validation loss : 1.0815742625729305; validation accuracy : 0.3723849372384937
Model 56:	 train loss : 1.0858489402622997; train accuracy : 0.3739551047243355; 
 validation loss : 1.083085091191777; validation accuracy : 0.36401673640167365
Model 57:	 train loss : 1.0776232116074462; train accuracy : 0.33868229672425476; 
 validation loss : 1.079414380194562; validation accuracy : 0.3389121338912134
Model 58:	 train loss : 1.0812771752843369; train accuracy : 0.3969598041216078; 
 validation loss : 1.0633657848706002; validation accuracy : 0.4351464435146444
Model 59:	 train loss : 1.08

Model 3:	 train loss : 1.075373116019679; train accuracy : 0.41410726026110645; 
 validation loss : 1.085209626125407; validation accuracy : 0.37656903765690375
Model 4:	 train loss : 1.0693465520599197; train accuracy : 0.40015330171783886; 
 validation loss : 1.0764113825056945; validation accuracy : 0.39330543933054396
Model 5:	 train loss : 1.0669141456251585; train accuracy : 0.3955574340189725; 
 validation loss : 1.0625353432904314; validation accuracy : 0.42677824267782427
Model 6:	 train loss : 1.0697174176865434; train accuracy : 0.4357914812460267; 
 validation loss : 1.0462103450133107; validation accuracy : 0.48535564853556484
Model 7:	 train loss : 1.0679413937708635; train accuracy : 0.4078235710505879; 
 validation loss : 1.0761171825557467; validation accuracy : 0.38493723849372385
Model 8:	 train loss : 1.0668360040815457; train accuracy : 0.41903201693411485; 
 validation loss : 1.0587387500777858; validation accuracy : 0.4560669456066946
Model 9:	 train loss : 1.072

...

Model 19:	 train loss : 0.5970005923935976; train accuracy : 0.9544626461072084; 
 validation loss : 0.6441229594414475; validation accuracy : 0.899581589958159
Model 20:	 train loss : 0.5921426595507023; train accuracy : 0.9616113329641182; 
 validation loss : 0.6548784274506845; validation accuracy : 0.895397489539749
Model 21:	 train loss : 0.5929942290865777; train accuracy : 0.9612979858337949; 
 validation loss : 0.6298393442736913; validation accuracy : 0.9205020920502092
Model 22:	 train loss : 0.6157203941242242; train accuracy : 0.9321348412860349; 
 validation loss : 0.623067987821684; validation accuracy : 0.9288702928870293
Model 23:	 train loss : 0.6147920647266792; train accuracy : 0.9380155653365202; 
 validation loss : 0.6670132431442335; validation accuracy : 0.8744769874476988
Model 24:	 train loss : 0.6338804487695633; train accuracy : 0.9164966333401346; 
 validation loss : 0.6814062362778995; validation accuracy : 0.8619246861924686
Model 25:	 train loss : 0.59232

Model 70:	 train loss : 0.6020541795434481; train accuracy : 0.9490045763255313; 
 validation loss : 0.6139750599577048; validation accuracy : 0.9330543933054394
Model 71:	 train loss : 0.6242396497879331; train accuracy : 0.9283309528667618; 
 validation loss : 0.7020552217659081; validation accuracy : 0.8368200836820083
Model 72:	 train loss : 0.6040219038985488; train accuracy : 0.9468184335558341; 
 validation loss : 0.6340890778715015; validation accuracy : 0.9205020920502092
Model 73:	 train loss : 0.6347034608441566; train accuracy : 0.9131882706153264; 
 validation loss : 0.6826371044560089; validation accuracy : 0.8702928870292888
Model 74:	 train loss : 0.604344931311594; train accuracy : 0.9476378322532168; 
 validation loss : 0.6485735215644591; validation accuracy : 0.899581589958159
Model 75:	 train loss : 0.605733995526633; train accuracy : 0.94392786700479; 
 validation loss : 0.666495513884061; validation accuracy : 0.8744769874476988
Model 76:	 train loss : 0.59747320

------------------------- Final result of the model 18 ! -------------------------
Train loss : 0.6187916686918372; Train accuracy : 0.9320255341475501; 
 Validation loss : 0.6288339113629242; Validation accuracy : 0.9205020920502092
------------------------- Final result of the model 19 ! -------------------------
Train loss : 0.6075233004743748; Train accuracy : 0.9430509808493893; 
 Validation loss : 0.6132600641686671; Validation accuracy : 0.9414225941422594
------------------------- Final result of the model 20 ! -------------------------
Train loss : 0.599462855567341; Train accuracy : 0.9523129390503395; 
 Validation loss : 0.6493214151258708; Validation accuracy : 0.9037656903765691
------------------------- Final result of the model 21 ! -------------------------
Train loss : 0.6050923895074791; Train accuracy : 0.9465779578511674; 
 Validation loss : 0.6224204366219163; Validation accuracy : 0.9330543933054394
------------------------- Final result of the model 22 ! --------

------------------------- Final result of the model 54 ! -------------------------
Train loss : 0.5927628089649446; Train accuracy : 0.9590964590964591; 
 Validation loss : 0.642860891265107; Validation accuracy : 0.9037656903765691
------------------------- Final result of the model 55 ! -------------------------
Train loss : 0.5981809576725111; Train accuracy : 0.9544990818200367; 
 Validation loss : 0.6232435782517181; Validation accuracy : 0.9288702928870293
------------------------- Final result of the model 56 ! -------------------------
Train loss : 0.6097655107201227; Train accuracy : 0.9393725932187471; 
 Validation loss : 0.6201062529830673; Validation accuracy : 0.9372384937238494
------------------------- Final result of the model 57 ! -------------------------
Train loss : 0.6495389609177709; Train accuracy : 0.9012001984029956; 
 Validation loss : 0.6513331874317345; Validation accuracy : 0.891213389121339
------------------------- Final result of the model 58 ! ---------

------------------------- Final result of the model 90 ! -------------------------
Train loss : 0.626955921006709; Train accuracy : 0.9213280088611654; 
 Validation loss : 0.641330020697677; Validation accuracy : 0.9163179916317992
------------------------- Final result of the model 91 ! -------------------------
Train loss : 0.6395686001188962; Train accuracy : 0.910579473576821; 
 Validation loss : 0.6857986246370362; Validation accuracy : 0.8619246861924686
------------------------- Final result of the model 92 ! -------------------------
Train loss : 0.600231886421899; Train accuracy : 0.9544626461072084; 
 Validation loss : 0.6263759105665008; Validation accuracy : 0.9163179916317992
------------------------- Final result of the model 93 ! -------------------------
Train loss : 0.6055171619250744; Train accuracy : 0.9455869064622381; 
 Validation loss : 0.6470261729744567; Validation accuracy : 0.9079497907949791
------------------------- Final result of the model 94 ! -----------

In [16]:
print("Training time = ", (end-start)/3600)

Training time =  1.8361966542402903


### Test part

In [17]:
test_accs = []
for i in range(len(test_dataset)):
    print("------------------------- Let's predict with model {} ! -------------------------".format(i+1))
    acc = testModel(models[i], test_dataset[i], devices[i])
    test_accs.append(mean(acc))
    print("------------------------- Model {} predict with {} of accuracy -------------------------".format(i+1, mean(acc)))

------------------------- Let's predict with model 1 ! -------------------------
------------------------- Model 1 predict with 0.9285714285714286 of accuracy -------------------------
------------------------- Let's predict with model 2 ! -------------------------
------------------------- Model 2 predict with 1.0 of accuracy -------------------------
------------------------- Let's predict with model 3 ! -------------------------
------------------------- Model 3 predict with 0.9583333333333334 of accuracy -------------------------
------------------------- Let's predict with model 4 ! -------------------------
------------------------- Model 4 predict with 1.0 of accuracy -------------------------
------------------------- Let's predict with model 5 ! -------------------------
------------------------- Model 5 predict with 1.0 of accuracy -------------------------
------------------------- Let's predict with model 6 ! -------------------------
------------------------- Model 6 predi

------------------------- Model 49 predict with 0.0 of accuracy -------------------------
------------------------- Let's predict with model 50 ! -------------------------
------------------------- Model 50 predict with 1.0 of accuracy -------------------------
------------------------- Let's predict with model 51 ! -------------------------
------------------------- Model 51 predict with 0.48 of accuracy -------------------------
------------------------- Let's predict with model 52 ! -------------------------
------------------------- Model 52 predict with 0.0 of accuracy -------------------------
------------------------- Let's predict with model 53 ! -------------------------
------------------------- Model 53 predict with 0.96 of accuracy -------------------------
------------------------- Let's predict with model 54 ! -------------------------
------------------------- Model 54 predict with 0.9583333333333334 of accuracy -------------------------
------------------------- Let's p

------------------------- Model 97 predict with 0.44 of accuracy -------------------------
------------------------- Let's predict with model 98 ! -------------------------
------------------------- Model 98 predict with 0.96 of accuracy -------------------------
------------------------- Let's predict with model 99 ! -------------------------
------------------------- Model 99 predict with 0.04 of accuracy -------------------------
------------------------- Let's predict with model 100 ! -------------------------
------------------------- Model 100 predict with 0.0 of accuracy -------------------------
------------------------- Let's predict with model 101 ! -------------------------
------------------------- Model 101 predict with 0.36 of accuracy -------------------------


In [18]:
total_acc = 0
for i in range(len(test_accs)):
    total_acc += test_accs[i]
print("The mean accuracy is {}".format(total_acc/len(test_accs))) 

The mean accuracy is 0.7774720340137775


## Distributed Data Parallel

### Utility functions

In [28]:
def setup(rank, world_size=5):
    os.environ['MASTER_ADDR'] = 'localhost'
    os.environ['MASTER_PORT'] = '12355'

    # initialize the process group
    dist.init_process_group("nccl", rank=rank, world_size=world_size)

def cleanup():
    dist.destroy_process_group()

In [16]:
def createCNN(rank, world_size):
    setup(rank, world_size)
    model = ConvNet()
    model = model.double()
    loss = nn.CrossEntropyLoss()
    
    if torch.cuda.is_available():
        cuda='cuda:'+str(rank)
        loss.cuda()
    device = torch.device(cuda if torch.cuda.is_available() else 'cpu')
    model.to(device)
    model = DDP(model, device_ids=[rank])
    optimizer = Adam(model.parameters(), lr=0.00020441990333108206)
    
    return model, loss, optimizer, device

In [17]:
def train(device, model, loss, optimizer, train_dataset, train_sampler, validation_dataset, validation_sampler, epochs, patience, path, rank, verbose=0, batch_size=338):
    train_losses = []
    val_losses = []
    train_acc = []
    val_acc = []
    min_val_loss = np.Inf
    max_val_acc = np.NINF
    epochs_no_improve_loss = 0
    epochs_no_improve_acc = 0
    if verbose == 1:
        verbScheduler = True
    else:
        verbScheduler = False
    scheduler = ReduceLROnPlateau(optimizer, factor=0.5, patience=80, cooldown=10, verbose=verbScheduler)
    training_generator = DataLoader(train_dataset, batch_size=batch_size, sampler=test_sampler)
    validation_generator = DataLoader(validation_dataset, batch_size=batch_size, sampler=validation_sampler)
    model.train()
    for epoch in range(epochs):
        loss_train_epoch = []
        acc_train_epoch = []
        for i, (ramanSpectraTrain, labelTrain) in enumerate(training_generator):
            ramanSpectraTrain = ramanSpectraTrain.to(device)
            labelTrain = labelTrain.to(device)
        
            optimizer.zero_grad()
        
            output_train = model(ramanSpectraTrain)
            
            loss_train = loss(output_train, labelTrain)
            loss_train_epoch.append(loss_train.cpu().item())
            
            loss_train.backward()
            optimizer.step()
            
            output_label = torch.argmax(output_train, dim=1)
            acc_train = accuracy_score(labelTrain.cpu().detach().numpy(), output_label.cpu().detach().numpy())
            acc_train_epoch.append(acc_train)
        
        loss_train = mean(loss_train_epoch)
        acc_train = mean(acc_train_epoch)
        train_losses.append(loss_train)
        train_acc.append(acc_train)
        
        with torch.no_grad():
            loss_val_epoch = []
            acc_val_epoch = []
            for j, (ramanSpectraVal, labelVal) in enumerate(validation_generator):
                ramanSpectraVal = ramanSpectraVal.to(device)
                labelVal = labelVal.to(device)
                    
                output_val = model(ramanSpectraVal)
                    
                loss_val = loss(output_val, labelVal)
                loss_val_epoch.append(loss_val.cpu().item())
                
                val_label = torch.argmax(output_val, dim=1)
                acc_val = accuracy_score(labelVal.cpu().detach().numpy(), val_label.cpu().detach().numpy())
                acc_val_epoch.append(acc_val)
            
            loss_val = mean(loss_val_epoch)
            acc_val = mean(acc_val_epoch)
        val_losses.append(loss_val)
        val_acc.append(acc_val)
        scheduler.step(loss_val)
        if acc_val > max_val_acc:
            epochs_no_improve_acc = 0
            max_val_acc = acc_val
            torch.save({'model_state_dict' : model.state_dict(),
                       'optimizer_state_dict' : optimizer.state_dict(),
                       'train_loss' : train_losses,
                       'train_acc' : train_acc,
                       'val_loss' : val_losses,
                       'val_acc' : val_acc}, path)
        else:
            epochs_no_improve_acc += 1
        
        if loss_val < min_val_loss:
            epochs_no_improve_loss = 0
            min_val_loss = loss_val
            torch.save({'model_state_dict' : model.state_dict(),
                       'optimizer_state_dict' : optimizer.state_dict(),
                       'train_loss' : train_losses,
                       'train_acc' : train_acc,
                       'val_loss' : val_losses,
                       'val_acc' : val_acc}, path)
        else:
            epochs_no_improve_loss += 1
            
        if verbose == 1 and rank == 0:
            print("Epoch {}:\t train loss : {}; train accuracy : {}; \n validation loss : {}; validation accuracy : {}".format(epoch+1, loss_train, acc_train, loss_val, acc_val))
            
        if epochs_no_improve_loss >= patience and epochs_no_improve_acc >= patience:
            print("Early stopping at epoch {}".format(epoch+1))
            break
    
    checkpoint = torch.load(path)
    model.load_state_dict(checkpoint['model_state_dict'])
    optimizer.load_state_dict(checkpoint['optimizer_state_dict'])
    train_losses = checkpoint['train_loss']
    train_acc = checkpoint['train_acc']
    val_losses = checkpoint['val_loss']
    val_acc = checkpoint['val_acc']
    
    if verbose == 1 and rank == 0:
        print("----- Final result of the model ! -----")
        print("Train loss : {}; Train accuracy : {}; \n Validation loss : {}; Validation accuracy : {}".format(train_losses[-1], train_acc[-1], val_losses[-1], val_acc[-1]))
    
    cleanup()
    return train_losses, val_losses, train_acc, val_acc

In [18]:
def run(rank, world_size, train_dataset, train_sampler, validation_dataset, validation_sampler, path):
    num_epochs = 2 #273
    patience = 50
    model, loss, optimizer, device = createCNN(rank, world_size)
    train_losses, val_losses, train_acc, val_acc = train(device, model, loss, optimizer, train_dataset, validation_dataset, epochs, patience, path, rank)
    return model, train_losses, val_losses, train_acc, val_acc

In [19]:
def testModel(model, test_set, test_sampler, device, batch_size=1):
    test_acc = []
    test_generator = DataLoader(test_set, batch_size=batch_size, sampler=test_sampler)
    model.eval()
    for i, (ramanSpectra, label) in enumerate(test_generator):
        ramanSpectra = ramanSpectra.to(device)
        label = label.to(device)
        
        labelPredict = model(ramanSpectra)
        labelPredict = torch.argmax(labelPredict, dim=1)
        
        acc = accuracy_score(label.cpu().detach().numpy(), labelPredict.cpu().detach().numpy())
        test_acc.append(acc)
    
    return test_acc

In [26]:
def globalTrain(rank, world_size, train_dataset, validation_dataset, test_dataset):
    models_list = []
    start = time.time()
    for i in range(len(train_dataset)):
        train_sampler = torch.utils.data.distributed.DistributedSampler(
            train_dataset[i],
            num_replicas=world_size,
            rank=rank
        )
        validation_sampler = torch.utils.data.distributed.DistributedSampler(
            validation_dataset[i],
            num_replicas=world_size,
            rank=rank
        )
        path = "../saved_models/covid_RAW/"+str(i+1)+".pckl"
        model, train_losses, val_losses, train_losses = run(rank, world_size, train_dataset[i], train_sampler, validation_dataset[i], validation_sampler, path)
        models_list.append(model)
    end = time.time()
    print("Training time :", (end-start)/3600)
    
    for i in range(len(test_dataset)):
        test_sampler = torch.utils.data.distributed.DistributedSampler(
            test_dataset[i],
            num_replicas=world_size,
            rank=rank
        )
        print("------------------------- Let's predict with model {} ! -------------------------".format(i+1))
        acc = testModel(models_list[i], test_dataset[i], test_sampler, devices[i])
        test_accs.append(mean(acc))
        print("------------------------- Model {} predict with {} of accuracy -------------------------".format(i+1, mean(acc)))

### Let's run

In [30]:
world_size = 4
mp.spawn(globalTrain, args=(world_size, train_dataset, validation_dataset, test_dataset), nprocs=world_size, join=True) 